# Exploratory analysis

TODO:
- Understanding the reason for fake profiles can bring insight on how to catch them (could be trivial with prior knowledge, e.g., SEO hacking => URLs)
- Make casistics (e.g. author publishing with empty orcid, author publishing but not on OpenAIRE, etc.)
- Temporal dimension of any use?
- Can we access private info thanks to the OpenAIRE-ORCID agreement?


In [73]:
import pandas as pd
import ast
import tldextract
import numpy

import plotly
from plotly.offline import iplot, init_notebook_mode
import plotly.graph_objs as go
import plotly.express as px

init_notebook_mode(connected=True)
TOP_N = 0
TOP_RANGE = [0, 0]
def set_top_n(n):
    global TOP_N, TOP_RANGE
    TOP_N = n
    TOP_RANGE = [-.5, n - 1 + .5]

Notable solid ORCID iDs for explorative purposes:

In [2]:
AM = '0000-0002-5193-7851'
PP = '0000-0002-8588-4196'


Anomalies ORCiD profile

In [3]:
JOURNAL = '0000-0003-1815-5732'
NOINFO= '0000-0001-5009-2052'
# todo: find group-shared ORCiD, if possible

Notable fake ORCID iDs for explorative purposes:

In [4]:
SCAFFOLD = '0000-0001-5004-7761'
WHATSAPP = '0000-0001-6997-9470'
PENIS = '0000-0002-3399-7287'
BITCOIN = '0000-0002-7518-6845'
FITNESS_CHINA = '0000-0002-1234-835X' # URL record + employment
CANNABIS = '0000-0002-9025-8632'      # URL > 70 + works (REMOVED)
PLUMBER = '0000-0002-1700-8311'       # URL > 10 + works 

Load the dataset

In [5]:
df = pd.read_csv('../data/raw/initial_info_whole.tsv', sep='\t', header=0,
                         names = ['orcid', 'claimed','verified_email', 'verified_primary_email', 
                                  'given_names', 'family_name', 'biography', 'other_names', 'urls', 
                                  'primary_email', 'other_emails', 'keywords', 'external_ids', 'education', 
                                  'employment', 'n_works', 'works_source'])

In [6]:
df[df.duplicated()]

orcid  claimed  verified_email  \
7552      0000-0001-7831-7567        1               1   
8416      0000-0001-8161-1345        1               1   
16498     0000-0002-1133-1505        1               1   
16830     0000-0002-1257-5536        1               1   
18835     0000-0002-2026-4156        1               1   
...                       ...      ...             ...   
10733293  0000-0002-9887-7788        1               1   
10737258  0000-0003-1367-8104        1               1   
10738308  0000-0003-1741-3437        1               1   
10741460  0000-0003-2909-8585        1               1   
10745078  0000-0003-4259-5324        1               1   

          verified_primary_email   given_names       family_name biography  \
7552                           1         Vahab            Vahdat       NaN   
8416                           1         AYFER      TEKIN ATACAN       NaN   
16498                          1      Xianrong               Lai       NaN   
16830                          1     Alexandra            Zimmer       NaN   
18835                          1         Fatma       Sri Wahyuni       NaN   
...                          ...           ...               ...       ...   
10733293                       1       Markéta        Laštůvková       NaN   
10737258                       1        LORENA  GUTIÉRREZ GARCÍA       NaN   
10738308                       1          Xing               Liu       NaN   
10741460                       1         Yusuf             Özcan       NaN   
10745078                       1  P Rama Mohan               NaN       NaN   

         other_names                                               urls  \
7552             NaN                                                NaN   
8416             NaN                                                NaN   
16498            NaN                                                NaN   
16830            NaN                                                NaN   
18835        ["Ayu"]                                                NaN   
...              ...                                                ...   
10733293         NaN                                                NaN   
10737258         NaN  [["LinkedIn", "https://www.linkedin.com/in/lor...   
10738308         NaN                                                NaN   
10741460         NaN                                                NaN   
10745078         NaN                                                NaN   

             primary_email other_emails  \
7552                   NaN          NaN   
8416                   NaN          NaN   
16498                  NaN          NaN   
16830                  NaN          NaN   
18835                  NaN          NaN   
...                    ...          ...   
10733293               NaN          NaN   
10737258  lorenagg@unex.es          NaN   
10738308               NaN          NaN   
10741460               NaN          NaN   
10745078               NaN          NaN   

                                                   keywords  \
7552                                                    NaN   
8416                                                    NaN   
16498                                                   NaN   
16830                                                   NaN   
18835                                                   NaN   
...                                                     ...   
10733293                                                NaN   
10737258  ["Agroecolog\u00eda, Bot\u00e1nica, Did\u00e1c...   
10738308                                                NaN   
10741460                                                NaN   
10745078                                                NaN   

                                               external_ids  \
7552      [["Scopus Author ID", "57193490305"], ["Scopus...   
8416                                                    NaN   
16498                 [["S

In [7]:
df.drop_duplicates(inplace=True)

Basic column manipulation (interpret columns as lists when necessary)

In [8]:
df['other_names'] = df[df.other_names.notna()]['other_names'].apply(lambda x: ast.literal_eval(x))

In [9]:
df['keywords'] = df[df.keywords.notna()]['keywords'].apply(lambda x: ast.literal_eval(x))

In [10]:
df['urls'] = df[df.urls.notna()]['urls'].apply(lambda x: ast.literal_eval(x))

In [11]:
df['other_emails'] = df[df.other_emails.notna()]['other_emails'].apply(lambda x: ast.literal_eval(x))

In [12]:
df['education'] = df[df.education.notna()]['education'].apply(lambda x: ast.literal_eval(x))

In [13]:
df['employment'] = df[df.employment.notna()]['employment'].apply(lambda x: ast.literal_eval(x))

In [14]:
df['external_ids'] = df[df.external_ids.notna()]['external_ids'].apply(lambda x: ast.literal_eval(x))

In [15]:
df['works_source'] = df[df.works_source.notna()]['works_source'].apply(lambda x: ast.literal_eval(x))

In [16]:
df.head(5)

orcid  claimed  verified_email  verified_primary_email  \
0  0000-0001-5000-2053        1               0                       0   
1  0000-0001-5000-6548        1               0                       0   
2  0000-0001-5000-7962        1               1                       1   
3  0000-0001-5000-8586        1               0                       0   
4  0000-0001-5001-0256        1               0                       0   

  given_names         family_name biography other_names urls primary_email  \
0      Jorge   Jaramillo Sanchez        NaN         NaN  NaN           NaN   
1     Wiseman            Bekelesi       NaN         NaN  NaN           NaN   
2       ALICE            INDIMULI       NaN         NaN  NaN           NaN   
3        shim              ji yun       NaN         NaN  NaN           NaN   
4      Sandro          Caramaschi       NaN         NaN  NaN           NaN   

  other_emails keywords external_ids education employment  n_works  \
0          NaN      NaN          NaN       NaN        NaN        0   
1          NaN      NaN          NaN       NaN        NaN        0   
2          NaN      NaN          NaN       NaN        NaN        0   
3          NaN      NaN          NaN       NaN        NaN        0   
4          NaN      NaN          NaN       NaN        NaN        0   

  works_source  
0          NaN  
1          NaN  
2          NaN  
3          NaN  
4          NaN

In [17]:
df[df['orcid'] == AM]

orcid  claimed  verified_email  verified_primary_email  \
8840413  0000-0002-5193-7851        1               1                       1   

        given_names family_name biography other_names  \
8840413      Andrea    Mannocci       NaN         NaN   

                                                      urls  \
8840413  [[Personal website, https://andremann.github.i...   

                       primary_email other_emails  \
8840413  andrea.mannocci@isti.cnr.it          NaN   

                                                  keywords  \
8840413  [Data science , science of science, scholarly ...   

                              external_ids  \
8840413  [[Scopus Author ID, 55233589900]]   

                                                 education  \
8840413  [[Information engineering, Ph.D., Università d...   

                                                employment  n_works  \
8840413  [[Research Associate, Istituto di Scienza e Te...       37   

                                              works_source  
8840413  [Scopus - Elsevier, Crossref Metadata Search, ...

In [18]:
df[df['orcid'] == WHATSAPP]

orcid  claimed  verified_email  verified_primary_email  \
9517099  0000-0001-6997-9470        1               1                       1   

        given_names family_name biography other_names  \
9517099       other    whatsapp       NaN         NaN   

                                                      urls primary_email  \
9517099  [[Otherwhatsapp, https://otherwhatsapp.com/], ...           NaN   

        other_emails                                           keywords  \
9517099          NaN  [Whatsapp GB, whatsapp gb 2020, whatsapp gb ba...   

        external_ids education employment  n_works works_source  
9517099          NaN       NaN        NaN        0          NaN

In [19]:
df.count()

orcid                     10744622
claimed                   10744622
verified_email            10744622
verified_primary_email    10744622
given_names               10716789
family_name               10437094
biography                   333885
other_names                 544550
urls                        688262
primary_email               121476
other_emails                 47470
keywords                    638634
external_ids               1285292
education                  2402440
employment                 2626670
n_works                   10744622
works_source               2671906
dtype: int64

In [20]:
df[df['orcid'] == '0000-0002-5154-6404']

orcid  claimed  verified_email  verified_primary_email  \
4595263  0000-0002-5154-6404        1               1                       1   
4595264  0000-0002-5154-6404        1               1                       1   

        given_names family_name biography other_names urls primary_email  \
4595263     Olusola    Bamisile       NaN         NaN  NaN           NaN   
4595264     Olusola    Bamisile       NaN         NaN  NaN           NaN   

        other_emails keywords external_ids  \
4595263          NaN      NaN          NaN   
4595264          NaN      NaN          NaN   

                                                 education  \
4595263  [[Energy Systems Engineering , Doctoral, Cypru...   
4595264  [[Energy Systems Engineering , Doctoral, Cypru...   

                                                employment  n_works  \
4595263  [[, University of Electronic Science and Techn...        3   
4595264  [[, University of Electronic Science and Techn...        2   

                                              works_source  
4595263  [Multidisciplinary Digital Publishing Institut...  
4595264                                         [Crossref]

In [21]:
df.drop(index=4595264, inplace=True)

In [22]:
df['orcid'].describe()

count                10744621
unique               10744621
top       0000-0001-8644-5622
freq                        1
Name: orcid, dtype: object

## Primary email

In [23]:
df['primary_email'].describe()

count                       121476
unique                      121473
top       patrick.davey@monash.edu
freq                             2
Name: primary_email, dtype: object

Dupe emails

In [24]:
df['primary_email'].dropna().loc[df['primary_email'].duplicated()]

7483666             maykin@owasp.org
9068234       opercin@erbakan.edu.tr
10246485    patrick.davey@monash.edu
Name: primary_email, dtype: object

In [25]:
df[df['primary_email'] == 'maykin@owasp.org']

orcid  claimed  verified_email  verified_primary_email  \
3776350  0000-0002-0836-2271        1               1                       1   
7483666  0000-0001-9855-1676        1               1                       1   

        given_names family_name biography other_names urls     primary_email  \
3776350      Maykin    Warasart       NaN         NaN  NaN  maykin@owasp.org   
7483666      Maykin    Warasart       NaN         NaN  NaN  maykin@owasp.org   

                                other_emails keywords external_ids education  \
3776350                   [maykin@dga.or.th]      NaN          NaN       NaN   
7483666  [maykin@dga.or.th, maykin@ieee.org]      NaN          NaN       NaN   

        employment  n_works works_source  
3776350        NaN        0          NaN  
7483666        NaN        0          NaN

In [26]:
df[df['primary_email'] == 'opercin@erbakan.edu.tr']

orcid  claimed  verified_email  verified_primary_email  \
3995032  0000-0002-2232-9638        1               1                       1   
9068234  0000-0003-0033-0918        1               1                       1   

        given_names family_name biography other_names urls  \
3995032       Osman      Perçin       NaN         NaN  NaN   
9068234       Osman      PERÇİN       NaN         NaN  NaN   

                  primary_email other_emails keywords external_ids education  \
3995032  opercin@erbakan.edu.tr          NaN      NaN          NaN       NaN   
9068234  opercin@erbakan.edu.tr          NaN      NaN          NaN       NaN   

                                                employment  n_works  \
3995032                                                NaN        0   
9068234  [[, Necmettin Erbakan University, Konya, , TR,...        0   

        works_source  
3995032          NaN  
9068234          NaN

In [27]:
df[df['primary_email'] == 'patrick.davey@monash.edu']

orcid  claimed  verified_email  \
5087745   0000-0002-8774-0030        1               1   
10246485  0000-0002-9158-1757        1               1   

          verified_primary_email given_names family_name biography  \
5087745                        1     Patrick       Davey       NaN   
10246485                       1     Patrick       Davey       NaN   

         other_names urls             primary_email other_emails  \
5087745          NaN  NaN  patrick.davey@monash.edu          NaN   
10246485         NaN  NaN  patrick.davey@monash.edu          NaN   

                                                   keywords external_ids  \
5087745                                                 NaN          NaN   
10246485  [Radiopharmaceuticals, Inorganic Chemistry, Bi...          NaN   

         education                                         employment  \
5087745        NaN  [[PhD Student, Monash University, Melbourne, V...   
10246485       NaN  [[PhD Student, Monash University, Melbourne, ,...   

          n_works works_source  
5087745         1   [Crossref]  
10246485        0          NaN

In [28]:
df['primary_email_domain'] = df['primary_email'].apply(lambda x: x.split('@')[1] if pd.notna(x) else x)

In [29]:
df['primary_email_domain'].describe()

count        121476
unique        17047
top       gmail.com
freq          25892
Name: primary_email_domain, dtype: object

In [30]:
primary_emails = df[['primary_email_domain', 'orcid']].groupby('primary_email_domain').count().sort_values('orcid', ascending=False)
primary_emails

orcid
primary_email_domain       
gmail.com             25892
hotmail.com            3674
yahoo.com              2578
163.com                2067
yuhs.ac                1124
...                     ...
iiap.gob.pe               1
iiap.org.pe               1
iibb.csic.es              1
iic.hokudai.ac.jp         1
zzuli.edu.cn              1

[17047 rows x 1 columns]

In [65]:
set_top_n(30)
data = [
    go.Bar(
        x=primary_emails[:TOP_N].sort_values(by=['orcid'], ascending=False).index,
        y=primary_emails[:TOP_N].sort_values(by=['orcid'], ascending=False)['orcid']
    )
]

layout = go.Layout(
    title='Top %s email domains' % TOP_N,
    xaxis=dict(tickangle=45, tickfont=dict(size=12), range=TOP_RANGE)
)
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig)

## Other emails

In [32]:
def extract_email_domains(lst):
    res = []
    for email in lst:
        res.append(email.split('@')[1])
    return res

In [33]:
df['other_email_domains'] = df['other_emails'].apply(lambda x: extract_email_domains(x) if isinstance(x, list) else x)

In [34]:
df[df['other_email_domains'].notna()].head()

orcid  claimed  verified_email  verified_primary_email  \
34    0000-0001-5011-9833        1               1                       1   
47    0000-0001-5017-1295        1               1                       1   
299   0000-0001-5109-3989        1               1                       1   
868   0000-0001-5320-1277        1               1                       1   
1176  0000-0001-5434-9994        1               1                       1   

     given_names family_name biography other_names urls  \
34          Mark     Kilbane       NaN         NaN  NaN   
47       Xinfeng        Tang       NaN         NaN  NaN   
299        colin      tysall       NaN         NaN  NaN   
868       Gökhan      KESKİN       NaN         NaN  NaN   
1176       Elena      Borucu       NaN         NaN  NaN   

                  primary_email                 other_emails keywords  \
34    mark.kilbane@seh.ox.ac.uk  [mark.kilbane@bsg.ox.ac.uk]      NaN   
47                          NaN   [tang.xinfeng@foxmail.com]      NaN   
299                         NaN       [colin.tysall@nhs.net]      NaN   
868   2012001598@stu.adu.edu.tr    [gokhankkeskin@gmail.com]      NaN   
1176       lenapasali@gmail.com      [epasali@yildiz.edu.tr]      NaN   

                           external_ids  \
34                                  NaN   
47    [[Scopus Author ID, 56927186900]]   
299                                 NaN   
868                                 NaN   
1176                                NaN   

                                              education  \
34    [[Blavatnik School of Government; St Edmund Ha...   
47    [[, , University of Hong Kong, Hong Kong, , HK...   
299                                                 NaN   
868                                                 NaN   
1176                                                NaN   

                                             employment  n_works  \
34                                                  NaN        0   
47                                                  NaN       11   
299   [[Associate Mental Health Act Manager, Coventr...        0   
868   [[, Adnan Menderes University, Aydin, , TR, gr...        0   
1176                                                NaN        0   

                           works_source primary_email_domain  \
34                                  NaN         seh.ox.ac.uk   
47    [Scopus - Elsevier, Xinfeng Tang]                  NaN   
299                                 NaN                  NaN   
868                                 NaN       stu.adu.edu.tr   
1176                                NaN            gmail.com   

     other_email_domains  
34        [bsg.ox.ac.uk]  
47         [foxmail.com]  
299            [nhs.net]  
868          [gmail.com]  
1176     [yildiz.edu.tr]

In [35]:
df['n_emails'] = df['other_emails'].str.len()

In [36]:
df.sort_values('n_emails', ascending=False)[['orcid', 'n_emails']]

orcid  n_emails
2039718   0000-0003-4171-3835      12.0
57198     0000-0001-6239-2968       9.0
10524509  0000-0003-2290-2817       7.0
7785216   0000-0003-2151-4089       7.0
3556386   0000-0001-9084-3156       6.0
...                       ...       ...
10747035  0000-0003-4998-1551       NaN
10747036  0000-0003-4998-4111       NaN
10747037  0000-0003-4998-6045       NaN
10747038  0000-0003-4998-8868       NaN
10747039  0000-0003-4999-7916       NaN

[10744621 rows x 2 columns]

In [37]:
grouped_other_emails = df[['orcid', 'other_email_domains']]\
                        .explode('other_email_domains')\
                        .reset_index(drop=True)\
                        .groupby('other_email_domains')\
                        .count()\
                        .sort_values('orcid', ascending=False)

In [74]:
set_top_n(30)
data = [
    go.Bar(
        x=grouped_other_emails[:TOP_N].sort_values(by=['orcid'], ascending=False).index,
        y=grouped_other_emails[:TOP_N].sort_values(by=['orcid'], ascending=False)['orcid']
    )
]

layout = go.Layout(
    title='Top %s other email domains' % TOP_N, 
    xaxis=dict(tickangle=45, tickfont=dict(size=12), range=TOP_RANGE)
)
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig)

## Email speculation

In [39]:
df[df['primary_email'].isna() & df['other_emails'].notna()]

orcid  claimed  verified_email  \
47        0000-0001-5017-1295        1               1   
299       0000-0001-5109-3989        1               1   
1296      0000-0001-5476-0126        1               1   
1429      0000-0001-5522-427X        1               1   
1628      0000-0001-5597-3115        1               1   
...                       ...      ...             ...   
10743658  0000-0003-3740-8352        1               1   
10744876  0000-0003-4192-6451        1               1   
10745274  0000-0003-4333-9728        1               1   
10745417  0000-0003-4383-4745        1               1   
10746702  0000-0003-4878-2737        1               1   

          verified_primary_email  given_names           family_name  \
47                             1      Xinfeng                  Tang   
299                            1        colin                tysall   
1296                           1  Aura Windy       Hernández Cetina   
1429                           1     Süleyman                  Özen   
1628                           1         Wade              Harrison   
...                          ...          ...                   ...   
10743658                       1          Rui                 Zhang   
10744876                       1   Sanjib Raj                Pandey   
10745274                       1        Mario  De la Fuente Lloreda   
10745417                       1          Jie                  Yang   
10746702                       1      Aleksey           Adamtsevich   

                                                  biography  \
47                                                      NaN   
299                                                     NaN   
1296                                                    NaN   
1429                                                    NaN   
1628                                                    NaN   
...                                                     ...   
10743658                                                NaN   
10744876                                                NaN   
10745274  Person in charge to coordinate the scientific ...   
10745417                                                NaN   
10746702                                                NaN   

                                 other_names  \
47                                       NaN   
299                                      NaN   
1296                                     NaN   
1429                                     NaN   
1628                                     NaN   
...                                      ...   
10743658                                 NaN   
10744876                                 NaN   
10745274  [M.de la Fuente, De la Fuente, M.]   
10745417                                 NaN   
10746702                                 NaN   

                                                       urls primary_email  \
47                                                      NaN           NaN   
299                                                     NaN           NaN   
1296                                                    NaN           NaN   
1429      [[Academic CV, https://akademik.yok.gov.tr/Aka...           NaN   
1628                                                    NaN           NaN   
...                                                     ...           ...   
10743658                                                NaN           NaN   
10744876  [[Personal, https://www.sanjibpandey.wix.com/p...           NaN   
10745274  [[researchgate profile, https://www.researchga...           NaN   
10745417                                                NaN           NaN   
10746702  [[Moscow State University of Civil Engineering...           NaN   

                               other_emails  \
47               [tang.xinfeng@foxmail.com]   
299                  [colin.tysall@nhs.net]   
1296           [u0902038@unimilitar.edu.co]   
1429             [suleyman.

## URLs

In [40]:
def extract_url_domains(lst):
    domains = []
    for e in lst:
        # e[0] is a string describing the url
        # e[1] is the url
        domain = tldextract.extract(e[1])
        domains.append(domain.registered_domain)
    return domains

In [41]:
df['url_domains'] = df['urls'].apply(lambda x: extract_url_domains(x) if isinstance(x, list) else x)

In [42]:
df[df['url_domains'].notna()].head()

orcid  claimed  verified_email  verified_primary_email  \
5   0000-0001-5001-4994        1               1                       1   
14  0000-0001-5004-7761        1               1                       1   
15  0000-0001-5005-0557        1               1                       1   
29  0000-0001-5009-8091        1               1                       1   
30  0000-0001-5010-9539        1               1                       1   

        given_names family_name  \
5             Siren        Rühs   
14      scaffolding        hire   
15              Sen          RT   
29         Gabriela     Madruga   
30  Sangram Keshari        Sahu   

                                            biography  \
5   I am an oceanographer studying the interannual...   
14                                                NaN   
15                                                NaN   
29  Possui graduação em Medicina Veterinaria pela ...   
30                                                NaN   

                                          other_names  \
5                                       [Siren Ruehs]   
14  [The first feature that you have to check in t...   
15                                                NaN   
29                          [Gabriela Morais Madruga]   
30                                          [sk-sahu]   

                                                 urls primary_email  ...  \
5   [[ResearchGate, https://www.researchgate.net/p...           NaN  ...   
14  [[scaffolding hire Wellington, https://www.tig...           NaN  ...   
15  [[Research on Psychology, psychiatry, Genetics...           NaN  ...   
29  [[Curriculo lattes, http://buscatextual.cnpq.b...           NaN  ...   
30           [[Academic webpage, https://sksahu.net]]           NaN  ...   

                                       keywords               external_ids  \
5                                           NaN                        NaN   
14                [scaffolding hire Wellington]                        NaN   
15                                          NaN                        NaN   
29                   [veterinary ophthalmology]                        NaN   
30  [Computational Genomics and Bioinformatics]  [[Loop profile, 1098977]]   

                                            education  \
5                                                 NaN   
14                                                NaN   
15                                                NaN   
29  [[Surgery in small animal, PhD, Universidade E...   
30  [[Centre for Bioinformatics, M.Sc. Bioinformat...   

                                           employment n_works  \
5                                                 NaN      11   
14                                                NaN       0   
15                                                NaN       0   
29  [[PhD , University of Minnesota, Minneapolis, ...      14   
30  [[Bioinformatics Junior Research Fellow, India...       3   

                                        works_source primary_email_domain  \
5                                       [Siren Rühs]                  NaN   
14                                               NaN                  NaN   
15                                               NaN                  NaN   
29                                [Gabriela Madruga]                  NaN   
30  [Crossref Metadata Search, Sangram Keshari Sahu]                  NaN   

   other_email_domains n_emails             url_domains  
5                  NaN      NaN      [researchgate.net]  
14                 NaN      NaN  [tigerscaffolds.co.nz]  
15                 NaN      NaN     [corticalbrain.com]  
29                 NaN      NaN               [cnpq.br]  
30                 NaN      NaN            [sksahu.net]  

[5 rows x 21 columns]

In [43]:
df['n_urls'] = df['url_domains'].str.len()

In [44]:
df.sort_values('n_urls', ascending=False)[['orcid', 'n_urls']]

orcid  n_urls
70577     0000-0002-1234-835X   219.0
5164541   0000-0001-7478-4539   174.0
1215225   0000-0002-7392-3792   169.0
10240510  0000-0002-6938-9638   152.0
4004281   0000-0002-5710-4041   114.0
...                       ...     ...
10747035  0000-0003-4998-1551     NaN
10747036  0000-0003-4998-4111     NaN
10747037  0000-0003-4998-6045     NaN
10747038  0000-0003-4998-8868     NaN
10747039  0000-0003-4999-7916     NaN

[10744621 rows x 2 columns]

In [75]:
set_top_n(100)
data = [
    go.Bar(
        x=df.sort_values(by=['n_urls'], ascending=False)['orcid'][:TOP_N],
        y=df.sort_values(by=['n_urls'], ascending=False)['n_urls'][:TOP_N]
    )
]

layout = go.Layout(
    title='Top %s ORCID with URLs' % TOP_N,
    xaxis=dict(tickangle=45, tickfont=dict(size=12), range=TOP_RANGE)
)
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig)

In [46]:
grouped_urls = df[['orcid', 'url_domains']]\
                .explode('url_domains')\
                .reset_index(drop=True)\
                .groupby('url_domains')\
                .count()\
                .sort_values('orcid', ascending=False)

In [77]:
set_top_n(30)
data = [
    go.Bar(
        x=grouped_urls[:TOP_N].sort_values(by=['orcid'], ascending=False).index,
        y=grouped_urls[:TOP_N].sort_values(by=['orcid'], ascending=False)['orcid']
    )
]

layout = go.Layout(
    title='Top %s URL domains' % TOP_N,
    xaxis=dict(tickangle=45, tickfont=dict(size=12), range=TOP_RANGE)
)
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig)

In [48]:
df[(df['url_domains'].str.len() > 50) & (df['n_works'] > 0)]

orcid  claimed  verified_email  \
482862    0000-0003-4948-9268        1               1   
554859    0000-0002-1929-6054        1               1   
1381092   0000-0002-9025-8632        1               1   
2679353   0000-0003-2407-3557        1               1   
3354430   0000-0002-3920-7389        1               1   
4004281   0000-0002-5710-4041        1               1   
4022480   0000-0003-2450-090X        1               1   
6335357   0000-0003-2593-7134        1               1   
6489838   0000-0002-9965-2425        1               1   
7570584   0000-0003-2183-8112        1               1   
10240510  0000-0002-6938-9638        1               1   
10448304  0000-0002-4062-3603        1               1   
10663894  0000-0002-3997-5070        1               1   

          verified_primary_email         given_names        family_name  \
482862                         1            Gustavo             Duperré   
554859                         1    Franklin Américo      Canaza Choque   
1381092                        1         buycannabis         dispensary   
2679353                        1               Abdul               Aziz   
3354430                        1                  А.              Гусев   
4004281                        1             Ryszard           Romaniuk   
4022480                        1              Eduard            Babulak   
6335357                        1                 Aan            Jaelani   
6489838                        1            Jaroslaw           Spychala   
7570584                        1       Pelayo Munhoz               Olea   
10240510                       1              Adolfo    Catral Sanabria   
10448304                       1       JUAN DE DIOS   BELTRÁN MANCILLA    
10663894                       1  Dr. Parameshachari                B D   

                                                  biography  \
482862    Gustavo Norberto Duperré graduated in Arts and...   
554859    Docente-Investigador Social. Maestrando en Der...   
1381092   We procure and deliver premium cannabis strain...   
2679353   Abdul Aziz was born on May 25, 1973, in Brebes...   
3354430   Surname, Name Gusev  Alexander LeonidovichDate...   
4004281   Professor of Electronics and Communications En...   
4022480   Professor Eduard Babulak is accomplished inter...   
6335357   All my papers can be downloaded from portal:Re...   
6489838   Jaroslaw Spychala has received a doctoral degr...   
7570584   Pós-Doutorado em Gestão Ambiental pela Univers...   
10240510  My education is in computer science, mathemati...   
10448304  JUAN DE DIOS BELTRÁN MANCILLA (*) Filósofo aut...   
10663894  Dr. Parameshachari B DACM Distinguished Speake...   

                                                other_names  \
482862           [Gustavo Norberto Duperré, Duperré, G. N.]   
554859    [Franklin Américo Canaza-Choque , Franklin A. ...   
1381092   [We procure and deliver premium cannabis strai...   
2679353   [Abdul Aziz, Aziz, Abdul, Aziz, A., Aziz, Abd,...   
3354430   [Alexander L. Gusev , Alexander Leonidovich Gu...   
4004281   [R.Romaniuk, R.S.Romaniuk, Ryszard Romaniuk, R...   
4022480                          [Professor Eduard Babulak]   
6335357                         [Jaelani, A., Jaelani, Aan]   
6489838                           [Jaroslaw Jozef Spychala]   
7570584   [ Munhoz, Pelayo Olea,  Olea, Pelayo,  Olea, P...   
10240510                                                NaN   
10448304  [Juan de Dios Beltrán Mancilla, FILÓSOFO AUTOD...   
10663894                           [Dr. PARAMESHACHARI B D]   

                                                       urls  \
482862    [[Gis in Cultural Heritage - ICOMOS România, h...   
554859    [[Consejo Nacional de Ciencia, Tecnología e In...   
1381092   [[find your cannabis & marijuana dispensary , ...   
2679353   [[Google Scholar, https://scholar.google.com/c...   
3354430   [[A.L. Gusev  Alternative Energy and Ecology, ...   
4004281   [[Scho

In [49]:
df[(df['url_domains'].str.len() > 10) & (df['n_works'] > 0) & (df['works_source'].str.len() == 1)]

orcid  claimed  verified_email  \
45566     0000-0003-1948-3180        1               1   
72674     0000-0002-2000-8339        1               1   
172820    0000-0001-9293-2224        1               1   
209505    0000-0003-3045-0056        1               1   
259877    0000-0003-1815-5732        1               1   
...                       ...      ...             ...   
10494820  0000-0002-1324-7171        1               1   
10495806  0000-0002-1700-8311        1               1   
10633545  0000-0003-2676-4431        1               1   
10648241  0000-0001-8157-0600        1               1   
10679699  0000-0002-9874-1450        1               1   

          verified_primary_email                given_names  \
45566                          1                       Mark   
72674                          1  Phòng khám tư nhân Hà Nội   
172820                         1                Juan Carlos   
209505                         1                     Ananda   
259877                         1                        JAS   
...                          ...                        ...   
10494820                       1             Vanesa Natalia   
10495806                       1                     Fix-IT   
10633545                       1                      Benny   
10648241                       1                      Bijan   
10679699                       1                    FENGZHI   

                         family_name  \
45566                           Katz   
72674                            NaN   
172820                  Garcia Hoyos   
209505                      Majumdar   
259877    (Jurnal Akuntansi Syariah)   
...                              ...   
10494820                   Rodriguez   
10495806                        Rite   
10633545                    Soewandi   
10648241                       Yavar   
10679699                          WU   

                                                  biography  \
45566     Mark N. Katz is a professor of government and ...   
72674                                                   NaN   
172820    My name is Juan Carlos García Hoyos. I was bor...   
209505    I am Ananda Majumdar, Child Care Educator at B...   
259877    JAS (Jurnal Akuntansi Syariah) published in pr...   
...                                                     ...   
10494820  Nombre y Apellido: Vanesa Natalia Rodriguez.  ...   
10495806                                                NaN   
10633545                                                NaN   
10648241  Senior Research Assistant and Phd Student in O...   
10679699                                                NaN   

                                                other_names  \
45566                                                   NaN   
72674                                                   NaN   
172820    [Juan Carlos Garcia Hoyos /, EXTRATERRANOVAS /...   
209505                                                  NaN   
259877                                                  NaN   
...                                                     ...   
10494820            [Vanesa Rodriguez, Vanesa N. Rodriguez]   
10495806                  [Best Heating & Plumbing Company]   
10633545                                   [Benny Soewandi]   
10648241                            [B. Yavar, Yavar Bijan]   
10679699                                                NaN   

                                                       urls primary_email  \
45566     [[Adjusting to Change: American Foreign Policy...           NaN   
72674     [[Sức khỏe, https://onhealth.vn/], [Khám phụ k...           NaN   
172820    [[Air Force Office of Scientific Research (WRI...           NaN   
209505    [[Migration Scholar and Ananda , https://grfdt...           NaN   
259877    [[Website, https://ejournal.stiesyariahbengkal...           NaN   
...                                                     ...           ...   
10494820  [[De rufianes y franchutas

In [50]:
exploded_sources = df[(df['url_domains'].str.len() > 10) & (df['n_works'] > 0) & (df['works_source'].str.len() == 1)].explode('works_source').reset_index(drop=True)
exploded_sources

orcid  claimed  verified_email  verified_primary_email  \
0    0000-0003-1948-3180        1               1                       1   
1    0000-0002-2000-8339        1               1                       1   
2    0000-0001-9293-2224        1               1                       1   
3    0000-0003-3045-0056        1               1                       1   
4    0000-0003-1815-5732        1               1                       1   
..                   ...      ...             ...                     ...   
134  0000-0002-1324-7171        1               1                       1   
135  0000-0002-1700-8311        1               1                       1   
136  0000-0003-2676-4431        1               1                       1   
137  0000-0001-8157-0600        1               1                       1   
138  0000-0002-9874-1450        1               1                       1   

                   given_names                 family_name  \
0                         Mark                        Katz   
1    Phòng khám tư nhân Hà Nội                         NaN   
2                  Juan Carlos                Garcia Hoyos   
3                       Ananda                    Majumdar   
4                          JAS  (Jurnal Akuntansi Syariah)   
..                         ...                         ...   
134             Vanesa Natalia                   Rodriguez   
135                     Fix-IT                        Rite   
136                      Benny                    Soewandi   
137                      Bijan                       Yavar   
138                    FENGZHI                          WU   

                                             biography  \
0    Mark N. Katz is a professor of government and ...   
1                                                  NaN   
2    My name is Juan Carlos García Hoyos. I was bor...   
3    I am Ananda Majumdar, Child Care Educator at B...   
4    JAS (Jurnal Akuntansi Syariah) published in pr...   
..                                                 ...   
134  Nombre y Apellido: Vanesa Natalia Rodriguez.  ...   
135                                                NaN   
136                                                NaN   
137  Senior Research Assistant and Phd Student in O...   
138                                                NaN   

                                           other_names  \
0                                                  NaN   
1                                                  NaN   
2    [Juan Carlos Garcia Hoyos /, EXTRATERRANOVAS /...   
3                                                  NaN   
4                                                  NaN   
..                                                 ...   
134            [Vanesa Rodriguez, Vanesa N. Rodriguez]   
135                  [Best Heating & Plumbing Company]   
136                                   [Benny Soewandi]   
137                            [B. Yavar, Yavar Bijan]   
138                                                NaN   

                                                  urls primary_email  ...  \
0    [[Adjusting to Change: American Foreign Policy...           NaN  ...   
1    [[Sức khỏe, https://onhealth.vn/], [Khám phụ k...           NaN  ...   
2    [[Air Force Office of Scientific Research (WRI...           NaN  ...   
3    [[Migration Scholar and Ananda , https://grfdt...           NaN  ...   
4    [[Website, https://ejournal.stiesyariahbengkal...           NaN  ...   
..                                                 ...           ...  ...   
134  [[De rufianes y franchutas Representaciones y ...           NaN  ...   
135  [[Website, https://fix-itrite.com], [Muckrack,...           NaN  ...   
136  [[Conservation Efforts as a Result of Theoreti...           NaN  ...   
137  [[Web of Science (Pub) Researcher ID: A-3544-2...           NaN  ...   
138  [[A Systematic Study on the Dynamic Softening ...           NaN  ...   

                          exte

In [51]:
exploded_sources[exploded_sources.apply(lambda x: x['works_source'].find(x['given_names']) >= 0, axis=1)]

orcid  claimed  verified_email  verified_primary_email  \
1    0000-0002-2000-8339        1               1                       1   
2    0000-0001-9293-2224        1               1                       1   
3    0000-0003-3045-0056        1               1                       1   
4    0000-0003-1815-5732        1               1                       1   
5    0000-0002-4379-6454        1               1                       1   
..                   ...      ...             ...                     ...   
132  0000-0001-6352-7086        1               1                       1   
133  0000-0002-4062-3603        1               1                       1   
134  0000-0002-1324-7171        1               1                       1   
136  0000-0003-2676-4431        1               1                       1   
138  0000-0002-9874-1450        1               1                       1   

                   given_names                 family_name  \
1    Phòng khám tư nhân Hà Nội                         NaN   
2                  Juan Carlos                Garcia Hoyos   
3                       Ananda                    Majumdar   
4                          JAS  (Jurnal Akuntansi Syariah)   
5             Caroline Wanjiru                     Kariuki   
..                         ...                         ...   
132                      Susan                   Hawthorne   
133              JUAN DE DIOS            BELTRÁN MANCILLA    
134             Vanesa Natalia                   Rodriguez   
136                      Benny                    Soewandi   
138                    FENGZHI                          WU   

                                             biography  \
1                                                  NaN   
2    My name is Juan Carlos García Hoyos. I was bor...   
3    I am Ananda Majumdar, Child Care Educator at B...   
4    JAS (Jurnal Akuntansi Syariah) published in pr...   
5    Caroline holds a PhD in Economics from Curtin ...   
..                                                 ...   
132  Susan is a poet, novelist, publisher and Sansk...   
133  JUAN DE DIOS BELTRÁN MANCILLA (*) Filósofo aut...   
134  Nombre y Apellido: Vanesa Natalia Rodriguez.  ...   
136                                                NaN   
138                                                NaN   

                                           other_names  \
1                                                  NaN   
2    [Juan Carlos Garcia Hoyos /, EXTRATERRANOVAS /...   
3                                                  NaN   
4                                                  NaN   
5                                                  NaN   
..                                                 ...   
132              [S. Hawthorne, Susan C. C. Hawthorne]   
133  [Juan de Dios Beltrán Mancilla, FILÓSOFO AUTOD...   
134            [Vanesa Rodriguez, Vanesa N. Rodriguez]   
136                                   [Benny Soewandi]   
138                                                NaN   

                                                  urls primary_email  ...  \
1    [[Sức khỏe, https://onhealth.vn/], [Khám phụ k...           NaN  ...   
2    [[Air Force Office of Scientific Research (WRI...           NaN  ...   
3    [[Migration Scholar and Ananda , https://grfdt...           NaN  ...   
4    [[Website, https://ejournal.stiesyariahbengkal...           NaN  ...   
5    [[Scopus Profile, https://www.scopus.com/dashb...           NaN  ...   
..                                                 ...           ...  ...   
132  [[Spinifex Press, http://www.spinifexpress.com...           NaN  ...   
133  [[01.- Juan de Dios Beltrán Mancilla. Teoría O...           NaN  ...   
134  [[De rufianes y franchutas Representaciones y ...           NaN  ...   
136  [[Conservation Efforts as a Result of Theoreti...           NaN  ...   
138  [[A Systematic Study on the Dynamic Softening ...           NaN  ...   

                      external

## Works source

Paste from Miriam

## External IDs

External IDs should come from reliable sources. ORCiD registrants cannot add them freely.

In [52]:
df['n_ids'] = df[df['external_ids'].notna()].external_ids.str.len()

In [53]:
df.n_ids.describe()

count    1.285292e+06
mean     1.357162e+00
std      6.607097e-01
min      1.000000e+00
25%      1.000000e+00
50%      1.000000e+00
75%      2.000000e+00
max      8.000000e+01
Name: n_ids, dtype: float64

In [54]:
df[df.n_ids == df.n_ids.max()]

orcid  claimed  verified_email  verified_primary_email  \
9228793  0000-0002-9554-6633        1               1                       1   

        given_names family_name biography other_names  \
9228793      John A    Williams       NaN         NaN   

                                                      urls primary_email  ...  \
9228793  [[Aston University profile page, https://resea...           NaN  ...   

        education                                         employment n_works  \
9228793       NaN  [[, Aston University, Birmingham, , GB, 1722, ...      91   

                      works_source primary_email_domain  other_email_domains  \
9228793  [Aston Research Explorer]                  NaN                  NaN   

        n_emails    url_domains n_urls  n_ids  
9228793      NaN  [aston.ac.uk]    1.0   80.0  

[1 rows x 23 columns]

In [55]:
ids = df[['orcid', 'external_ids']].explode('external_ids').reset_index(drop=True)

In [78]:
ids['provider'] = ids[ids.external_ids.notna()]['external_ids'].apply(lambda x: x[0])

In [79]:
ids[ids.provider.notna()].head()

orcid                     external_ids          provider
13  0000-0001-5004-4608  [Scopus Author ID, 40661094300]  Scopus Author ID
24  0000-0001-5008-2479  [Scopus Author ID, 12789856200]  Scopus Author ID
25  0000-0001-5008-2479     [Ciência ID, 2F1C-479B-B071]        Ciência ID
31  0000-0001-5010-9539          [Loop profile, 1098977]      Loop profile
42  0000-0001-5013-6529   [Scopus Author ID, 8986698300]  Scopus Author ID

In [80]:
data = [
    go.Bar(
        x=ids.groupby('provider').count().sort_values('orcid', ascending=False).index,
        y=ids.groupby('provider').count().sort_values('orcid', ascending=False)['orcid']
    )
]

layout = go.Layout(
    title='IDs provided',
    xaxis=dict(tickangle=45, tickfont=dict(size=12))
)
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig)

In [81]:
pd.unique(ids['provider'])

array([nan, 'Scopus Author ID', 'Ciência ID', 'Loop profile',
       'ResearcherID', 'Researcher Name Resolver ID', 'UOW Scholars',
       '中国科学家在线', 'Pitt ID', 'AuthenticusID', 'Sciprofile', 'GND', 'ISNI',
       'HKU ResearcherPage', 'CTI Vitae', 'Researcher ID', 'ID Dialnet',
       'Digital author ID', 'HKUST Profile',
       'Technical University of Denmark CWIS', 'Scopus Author ID: ',
       'Digital Author ID (DAI)', 'Scopus Author ID:', 'Google Scholar',
       'AuthID', 'Digital Author ID', 'iAuthor', 'US EPA VIVO', 'GitHub',
       'Scopus author ID', 'Chalmers ID', 'Scopus ID', 'Authenticus',
       'VIVO Cornell', 'Scopus  ID', 'ScienceOpen',
       'Smithsonian Profiles', 'ResearcherID:', 'DAI', 'eScientist',
       'KAKEN', 'Digital author ID (DAI)', 'ORCID', 'ID Dialnet:',
       'Dialnet ID', 'UNE Researcher ID', 'ResearcherID: ',
       'Profile system identifier', 'Custom', 'ResearcherId', 'ORCID iD'],
      dtype=object)

## Keywords

In [82]:
df['n_keywords'] = df.keywords.str.len()

In [83]:
df.sort_values('n_keywords', ascending=False)[['orcid', 'n_keywords']]

orcid  n_keywords
1681310   0000-0002-0673-0341       154.0
7717699   0000-0002-7060-4112       141.0
4597674   0000-0002-6075-3501       140.0
2066580   0000-0002-4071-0301       118.0
3531030   0000-0002-9638-8091       115.0
...                       ...         ...
10747035  0000-0003-4998-1551         NaN
10747036  0000-0003-4998-4111         NaN
10747037  0000-0003-4998-6045         NaN
10747038  0000-0003-4998-8868         NaN
10747039  0000-0003-4999-7916         NaN

[10744621 rows x 2 columns]

In [84]:
data = [
    go.Bar(
        x=df.sort_values('n_keywords', ascending=False)['orcid'][:100],
        y=df.sort_values('n_keywords', ascending=False)['n_keywords'][:100]
    )
]

layout = go.Layout(
    title='Keywords provided',
    xaxis=dict(tickangle=45, tickfont=dict(size=12))
)
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig)

## Correlation

In [85]:
fig = px.imshow(df[df.n_ids > 0].corr())
fig.show()